# Space-time partial differential equation: Study of the diffusive equation (implicit methods)

In [1]:
# Importing relevant libraries 
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt 
from nm_lib import nm_lib as nm
from matplotlib import animation
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# plt.style.use('dark_background')
plt.style.use('default')

def u(x, A=0.3): 
    """ 
    Initial condition for t=t0 when a = const

    Parameters
    ----------
    x : `array`
        Spatial axis. 
    A : `float`
        A constant of the initial condition (default = 0.02).
    
    Returns
    -------
    Equation 2
    """
    W = 0.1 
    x0 = 0
    return A*np.exp(-(x - x0)**2 / W**2)
    
x0 = -2.6 
xf = -x0

Let's consider now the viscous term in Burger's equation: 

$$\frac{\partial u}{\partial t} = \nu \frac{\partial^2 u}{\partial x^2}, \tag{1}$$

## 1- Apply an explicit method. 

What would be the CFL condition for a viscous term where $\nu$ is either a constant or an array that depends on $x$. We would like to solve equation (1) numerically for $x  [x_0, x_f]$ with $x_0 = −2.6$, $x_f = 2.6$, periodic boundary conditions and with the initial condition:

$$u(x,t=t_0) = A\exp(-(x-x_0)^2/W^2)   \tag{2}$$

with $A=0.3$, $W=0.1$, and $x_0=0$. __Suggestion__: Apply the first derivative upwind and the second downwind. Apply Von Newman analysis. Is it stable? What is the time-step dependence with $\Delta x$? 

<span style="color:pink">
We begin by applying the upwind and downwind derivative such that 

$$
\frac{u_j^{n+1} - u_j^n}{\Delta t} = \nu\frac{(u_{j+1}^n - 2u_j^n + u_{j-1}^n)}{\Delta x^2}
$$

Next, we apply Von-Newman analysis, 

$$
u_j^n = \xi^n e^{ikj\Delta x}, 
$$

which makes 

$$
e^{ikj\Delta x} \frac{\xi^{n+1} - \xi^n}{\Delta t} = \nu\xi^n e^{ikj\Delta x} \frac{e^{ik\Delta x} - 2 + e^{-ik\Delta x}}{\Delta x^2}. 
$$

We divide by $e^{ikj\Delta x}$ on both sides, to eliminate the term. 

$$
\frac{\xi^{n+1} - \xi^n}{\Delta t} = \nu\xi^n \frac{e^{ik\Delta x} - 2 + e^{-ik\Delta x}}{\Delta x^2}. 
$$

Next, we can rewrite the equation using that $e^{i\theta} = \cos\theta + i\sin\theta$, to get 

$$
\xi = 4\frac{\nu\Delta t}{\Delta x^2} \sin^2\left(\frac{k\Delta x}{2}\right) + 1.
$$

Requiering that $|\xi^n|^2 \leq 1$ for all $k$ means that 

$$
\left(4\frac{\nu\Delta t}{\Delta x^2} \sin^2\left(\frac{k\Delta x}{2}\right) + 1\right)^2 \leq 1
$$

This holds for all $k$ when, 

$$
\frac{16\nu^2\Delta t^2}{\Delta x^4} - \frac{4\nu\Delta t}{\Delta x^2} + 1 \leq 1 \\ 
\frac{16\nu^2\Delta t^2}{\Delta x^4} \leq \frac{4\nu\Delta t}{\Delta x^2} \\ 
\frac{4\nu\Delta t}{\Delta x^2} \leq 1, 
$$

making the CFL condition 

$$
\Delta t \leq \frac{\Delta x^2}{4\nu}. 
$$


</span>

How many steps are needed to reach a $t=1.8$ for $nump=128$? And $256$? 

In [2]:
## Code for that? 

# Initialize xx, t and unnt 
# nump = 128 
# nump = 256 
# xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0

# nt = 200 
# a = 1
# t, unnt, errt, countt = nm.(xx, u(xx), a, dt, nt, ddx = nm.deriv_cent, bnd_limits=[1,1], bnd_type='wrap')

## Choose one of the following options: 

## 2- Implicit methods.

In the [wiki](https://github.com/AST-Course/AST5110/wiki/Implicit-methods), we describe some implicit or semi-explicit methods that allow relaxing the CFL constraint on diffusive terms. Consider Newton-Rapson method and repeat the previous numerical experiment. For this, you will need to implement the following   


$F_j = u^{n+1}_j - u^n_j - \nu \, (u^{n+1}_{j+1} - 2u^{n+1}_{j}+u^{n+1}_{j-1})\frac{\Delta t}{\Delta x^2}$

in `NR_f` and `step_diff_burgers` functions in `nm_lib`. 

And the Jacobian can be easily built. 

$J(j,k) = F_j'(u^{n+1}_k)$

fill in the `jacobian` function in `nm_lib`. Note that this matrix is linear with $u$. 

In [3]:
# Initialize xx, t and unnt 
nint = 128
nump = nint + 1
xx = np.arange(nump)/(nump-1.0) * (xf - x0) + x0

nt = 200 
a = 1
dt = 1
t, unnt, errt, countt = nm.Newton_Raphson(xx, u(xx), a, dt, nt, bnd_limits=[1,1], bnd_type='wrap')

In [4]:
# Animation 
fig, axes = plt.subplots(nrows=1, ncols=1, figsize=(10, 5))

def init(): 
    xx,unnt[:,0]
    # axes.plot(xx,unnt[:,0])

def animate(i):
    axes.clear()
    axes.plot(xx,unnt[:,i])
    axes.set_title('t=%.2f'%t[i])
    # axes.set_ylim((0,0.35))
    axes.grid(True)

anim = FuncAnimation(fig, animate, interval=1, frames=nt, init_func=init)
plt.close()
HTML(anim.to_jshtml())

Test the model with [wiki](https://github.com/AST-Course/AST5110/wiki/Self-similar-solution-for-parabolic-eq) self-similar solutions. How long it takes each time step compared to the Lax-method? Use `time.time` library. Do it for nump=256, nt=30 and dt = 0.1. In order to test the simulation, use `curve_fit` from `scipy.optimize`. 

__hint__ consider to use a good initial guess (`p0`) in and `bnd_limits` to facilitate the fitting wiht `curve_fit`. What happens to the solution when increasing dt? How much can be improved in limiting the tolerance?

----------------------------------------------

Let's consider a non-linear function where $\nu$ depends on $u$. To keep it simple, solve the following: 

$\frac{\partial u}{\partial t} = u \frac{\partial^2 u}{\partial x^2}$

where $\nu_0$ is a constant and the same initial conditions as the previous exercise (fill in `Newton_Raphson_u`, `jacobian_u` and `NR_f_u`. Consider an error limit of $10^{-4}$ and compare the previous exercise (with the same error limit). How many iterations needs now the method to converge to the right solution? Why? Increase `ncount` to 1000. 

## 3- Semi-explicit methods. 

__a)__ Super-time-stepping (STS) schemes work for parabolic terms. STS is an API method that performs a subset of "unstable" intermediate steps, but the sum of all the steps is stable. Visualize how `taui_sts` varies with $nu$ and $niter$. Compare the solution with the analytical one for the final and intermediate STS steps. For the full STS steps, how improves the solution with $nu$? and $niter$? Is there a relation between the error and these two parameters, $nu$, and $niter$? For which $niter$ and $nu$ the method provides larger steps than an ordinary explicit. For this exercise, fill in `evol_sts`, and `taui_sts`. 